<a href="https://colab.research.google.com/github/ShenggKai/Kaggle_TempoRun/blob/master/Notebook/%5BTempoRun%5D_Information_Retrieval.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Download data

In [1]:
import json

#Download lyrics
!gdown --id 1V7WxGaVv3UamD4AM5qnqDNzkBSw6paQy
#Download queries
!gdown --id 1srNAjKMTncZUgxDTZZHfMnTbPd9ic2xx

Downloading...
From: https://drive.google.com/uc?id=1V7WxGaVv3UamD4AM5qnqDNzkBSw6paQy
To: /content/2335_Songs.json
100% 4.33M/4.33M [00:00<00:00, 98.2MB/s]
Downloading...
From: https://drive.google.com/uc?id=1srNAjKMTncZUgxDTZZHfMnTbPd9ic2xx
To: /content/500_queries.json
100% 39.0k/39.0k [00:00<00:00, 38.9MB/s]


# Preliminaries & Corpus Creation

In [2]:
# Install required libraries
!pip install rank-bm25

In [3]:
!pip install -q tf-models-official==2.3.0

     |████████████████████████████████| 840 kB 5.3 MB/s 
     |████████████████████████████████| 352 kB 28.1 MB/s 
     |████████████████████████████████| 234 kB 46.1 MB/s 
     |████████████████████████████████| 99 kB 8.5 MB/s 
     |████████████████████████████████| 47.8 MB 74 kB/s 
     |████████████████████████████████| 1.1 MB 23.3 MB/s 
     |████████████████████████████████| 1.2 MB 25.2 MB/s 
     |████████████████████████████████| 462 kB 37.8 MB/s 


In [ ]:
import pandas as pd


In [ ]:

df = pd.read_json (r'/content/2335_Songs.json')
df.to_csv (r'/content/sample_data/data.csv', index = None)

In [ ]:
df["song_id"].head(100)

0       0
1       1
2       2
3       3
4       4
     ... 
95    155
96    156
97    157
98    158
99    159
Name: song_id, Length: 100, dtype: int64

In [ ]:
# Import required libraries
import os
import pprint as pp
import numpy as np
import json
import tensorflow as tf 
from gensim.corpora import WikiCorpus
from rank_bm25 import BM25Okapi, BM25Plus

from official.modeling import tf_utils
from official import nlp
from official.nlp import bert

# Load the required submodules
import official.nlp.optimization
import official.nlp.bert.bert_models
import official.nlp.bert.configs
import official.nlp.bert.run_classifier
import official.nlp.bert.tokenization
import official.nlp.data.classifier_data_lib
import official.nlp.modeling.losses
import official.nlp.modeling.models
import official.nlp.modeling.networks

In [ ]:
from tqdm import tqdm
# link to data
CORPUS_SONG_JSON = "2335_Songs.json"
QUERIES_JSON = "500_queries.json"

In [ ]:
with open(CORPUS_SONG_JSON, 'r', encoding='utf-8') as fo:
  corpus_data = json.load(fo)

with open(QUERIES_JSON, 'r', encoding='utf-8') as fo:
  queries_test = json.load(fo)

In [ ]:
corpus_data

In [ ]:
corpus_data[1]["lyrics"]

'Từ ngày con ra đi\nCha lòng buồn thương nhớ\nCô đơn và sầu muộn\nBao ngày tháng mong chờ\nTừ ngày con ra đi\nTới thời gian bây giờ\nThấm thoát mười hai năm chẵn\nCha thường đứng ngồi ngẩn ngơ\nMẹ con không còn nữa\nĐi rồi quên từ giã\nCha một mình thui thủi\nLạnh giá và đơn côi\nNay con ở phương xa\nĐừng quên nơi quê nhà\nVẫn còn người trông đợi\nNgười ấy là cha già\nCha chờ con trong hấp hối\nLá thư cuối cùng con ơi\nThư này mong con nhận được\nThương con vất vả đơn côi\nMưa lạnh ngoài trời đang rơi\nGắng thêm một chút tàn hơi\nCha đây nhắn lại một lời\nChúc con hạnh phúc trọn đời trở lại\nThư này cuối cùng con ơi\nMẹ con đưa tay vẫy gọi\nBao năm cha đây trông đợi\nMẹ đón cha về chung đôi\nNhớ lời cha dặn con ơi\nHiến mình giúp đời yên vui\nDù xa cách biệt phương trời\nChớ quên tổ quốc giống nòi'

In [ ]:
queries_test


In [ ]:
print(corpus_data[:10])




[{'author': 'Trần Bình', 'title': 'Tình Yêu Thuỷ Chung', 'lyrics': 'Bài hát: Tình Yêu Thuỷ Chung - Trần Bình, Việt Linh\nCó phải là duyên khi anh gặp em\nTừ kiếp trước, thề ước chung đôi\nCùng hân hoan\nNhìn nhau đắm đuối\nLòng quyến luyến,\nChuyện mãi không thôi\nEm từ nơi đâu đã đến nơi này\nAnh hân hoan\nTrao Em vòng tay\nVà đôi ta,\nSống chung hạnh phúc\nCùng xây đắp,\nCho mối duyên này\nEm ơi Em ơi, dù phong ba\nDù bão tố, dù nắng cháy\nAnh vẫn yêu Em, mãi mãi không thôi\nAnh ơi Anh ơi, dù gian nan\nDù khốn khó Ta vẫn yêu nhau,\nĐến cuối cuộc đời\nTa vẫn bên nhau qua bao buồn vui\nTa yêu nhau, tình yêu đắm say\nTình yêu ta đẹp, tình yêu thắm thiết\nHạnh phúc trăm năm\nTình yêu thuỷ chung\n \n', 'song_id': '0000'}, {'author': 'Trần Bình', 'title': 'Lá Thư Của Cha', 'lyrics': 'Bài hát: Lá Thư Của Cha - Trần Bình\nTừ ngày con ra đi\nCha lòng buồn thương nhớ\nCô đơn và sầu muộn\nBao ngày tháng mong chờ\nTừ ngày con ra đi\nTới thời gian bây giờ\nThấm thoát mười hai năm chẵn\nCha thường

In [ ]:
strash_phrases = ['[', ']', 'intro', 'verse', 'ver', 'hook', 'đk', 'dk', ':']
for i in range(2335):
  for phrase in strash_phrases:
    while phrase in corpus_data[i]['lyrics']:
      l = r = corpus_data[i]['lyrics'].find(phrase)
      print(l)

In [ ]:
#Làm sạch dữ liệu 
strash_phrases = ['[', ']', 'intro', 'verse', 'ver', 'hook', 'đk', 'dk', ':'] #, 'chorus', 'pre-chorus']
#strash_sign = ['.', ',', '(', ')', '?',]

for i in range(2335):

  for phrase in strash_phrases:
    while phrase in corpus_data[i]['lyrics']:
      l = r = corpus_data[i]['lyrics'].find(phrase)

      while l != 0 and corpus_data[i]['lyrics'] [l] != '\n':
        l -= 1
      if l != 0:
        l += 1
      
      length = len(corpus_data[i]['lyrics'])

      while r < length and corpus_data[i]['lyrics'][r] != '\n':
        r += 1
      
      corpus_data[i]['lyrics'] = (corpus_data[i]['lyrics'][:l] + corpus_data[i]['lyrics'][r + 1:])

  #for sign in strash_sign:
   # corpus_data[i]['lyrics'] = corpus_data[i]['lyrics'].replace(sign, '')

In [ ]:
#Danh sách bài hát thiếu từ
lst = []
id = []
for i in range(2335):
  if '*' in corpus_data[i]['lyrics']:
    id.append(i)
    lst.append(corpus_data[i]['song_id'])




In [ ]:
for i in range(0,20):
  print(corpus_data[id[i]])

{'author': 'Đỗ Minh Hiếu', 'title': 'Mùa Xuân Tình Yêu', 'lyrics': 'Em ơi! Con sông, dòng suối tuy chưa hề nói có chung cội nguồn \nEm ơi! khi ta nhìn nhau yêu thương tràn về thác đổ, con sông dạt dào sóng vỗ miên man. \nEm ơi! Xuân nay vừa tới, xuân không hề nói chỉ chao nụ hồng.\n Em ơi! qua bao ngày đông, xuân nay lại về nhắc nhở, bao nhiêu là điều để nhớ, để thương. \nMùa xuân đến, nhắc ta những ngày bên sân trường lúc nắng mưa. \nMùa xuân đến, nhắc ta những điều mà ta chưa nói ra. \nMùa xuân đến nhắc ta những lần trên con đường phố *** và hôm nay, \nbước trên phố này, dường như nghe tiếng trái tim mình hát ca.', 'song_id': '0004'}
{'author': 'Mai Xuân Việt', 'title': 'Tiếng Ca Đàn Chim Việt', 'lyrics': 'Mênh mông hương lúa vàng\nNgát thơm khói lam chiều\nÊm đềm ngân nga tiếng tiêu\nDòng nước tắm mát cánh đồng xanh\nUốn lượn quanh qua làng thôn, chợ quê\nBan mai tia nắng hồng lá rơi lối em về\nThu vàng mang bao vấn vương\nTà áo lướt thướt tóc vờn bay\nTheo làn mây khi chiều buông đ

In [ ]:
def read_corpus(corpus_data):
    """
    Function that iteratively reads the saved articles from the corpus directory
    and appends the text to a list.
    
    Parameters
    ----------
    @param corpus_directory: str,
        A valid string specifying the path to the local directory in which the 
        files were saved using make_corpus().
        
    Returns
    -------
    @return corpus, list
        A list containing the text of an article in each element.
    """
    
    # Initialize empty corpus list
    corpus = []
    
    # For each file in the corpus directory, do...
    print("Reading local corpus, please wait...")

    for song in corpus_data:
      if song["lyrics"].split("\n")[0].startswith("Bài hát: "):
          lyric = "\n".join(song["lyrics"].split("\n")[1:])
      else:
          lyric = song["lyrics"]
      corpus.append([song["song_id"], lyric])
        
    # Done, return
    print("Done!")
    return corpus

In [ ]:
# Read corpus! 
corpus = read_corpus(corpus_data)

# Look at some example...
corpus[2]

# For some reason (only in Google Colab), this cell might need to be stopped
# for the first run, then run again. 

Reading local corpus, please wait...
Done!


['0002',
 'Đoạn buồn cho tôi biết mấy\nNgười tình rời xa tôi khuất bóng\nBiết cô đơn dâng ngập nỗi sầu \nRồi từng chiều mấy đen tim tím\nMột mình buồn tôi bước đơn côi \nMang trong tim nỗi nhớ một mình\nCho trời chiều buồn mênh mang\nLang thang mình tôi bước trên nỗi sầu\nĐi đâu về đâu muôn lối vô định\nĐoạn buồn biết mấy trong tôi\nNhớ người không nhớ đến tôi\nChiều tím tôi gọi tên ai \nĐoạn buồn cho tôi biết mấy\nHẹn hò em đã ngó lơ\nChiều nay tôi đứng một mình\nDòng người đua chen khắp chốn\nNhìn hoài không thấy em sang\nCho tôi đoạn buồn tình nhân.\n \n']

In [ ]:
corpus

# BM25 Implementation

In [ ]:
!pip install underthesea
!pip install pyvi

     |████████████████████████████████| 7.6 MB 4.7 MB/s 
     |████████████████████████████████| 235 kB 48.3 MB/s 
     |████████████████████████████████| 743 kB 30.8 MB/s 
     |████████████████████████████████| 581 kB 41.7 MB/s 
     |████████████████████████████████| 8.5 MB 5.2 MB/s 


In [ ]:
# Tokenize the corpus
from underthesea import word_tokenize

tokenized_corpus = []
for doc in tqdm(corpus):
  tokenize_lyric = word_tokenize(doc[-1]) 
  tokenize_lyric.append(f"-->{doc[0]}")
  tokenized_corpus.append(tokenize_lyric)

100%|██████████| 2335/2335 [00:34<00:00, 67.42it/s]


In [ ]:
tokenized_corpus

[['Có',
  'phải',
  'là',
  'duyên',
  'khi',
  'anh',
  'gặp',
  'em',
  'Từ',
  'kiếp',
  'trước',
  ',',
  'thề ước chung',
  'đôi',
  'Cùng',
  'hân hoan',
  'Nhìn',
  'nhau',
  'đắm đuối',
  'Lòng',
  'quyến luyến',
  ',',
  'Chuyện',
  'mãi',
  'không',
  'thôi',
  'Em',
  'từ',
  'nơi',
  'đâu',
  'đã',
  'đến',
  'nơi',
  'này',
  'Anh',
  'hân hoan',
  'Trao',
  'Em',
  'vòng tay',
  'Và',
  'đôi ta',
  ',',
  'Sống',
  'chung',
  'hạnh phúc',
  'Cùng',
  'xây đắp',
  ',',
  'Cho',
  'mối',
  'duyên',
  'này',
  'Em',
  'ơi',
  'Em',
  'ơi',
  ',',
  'dù',
  'phong ba',
  'Dù',
  'bão tố',
  ',',
  'dù',
  'nắng',
  'cháy',
  'Anh',
  'vẫn',
  'yêu',
  'Em',
  ',',
  'mãi mãi',
  'không',
  'thôi',
  'Anh',
  'ơi',
  'Anh',
  'ơi',
  ',',
  'dù',
  'gian nan',
  'Dù',
  'khốn khó',
  'Ta',
  'vẫn',
  'yêu',
  'nhau',
  ',',
  'Đến',
  'cuối',
  'cuộc đời',
  'Ta',
  'vẫn',
  'bên',
  'nhau',
  'qua',
  'bao',
  'buồn',
  'vui',
  'Ta',
  'yêu',
  'nhau',
  ',',
  'tình yêu',
 

In [ ]:
# Instantiate BM25 object from the tokenized corpus
bm25 = BM25Okapi(tokenized_corpus)

In [ ]:
#hàm a nhận một truy vấn chuỗi và đánh số `n` kết quả bắt buộc, 
#và trả về kết quả có liên quan nhất` n` từ kho dữ liệu của chúng ta:
def bm25okapi_search(tokenized_query, bm25, corpus, n_results = 1):
    """
    Function that takes a tokenized query and prints the first 100 words of the 
    n_results most relevant results found in the corpus, based on the BM25
    method.
    
    Parameters
    ----------
    @param tokenized_query: list, array-like
        A valid list containing the tokenized query.
    @param bm25: BM25 object,
        A valid object of type BM25 (BM25Okapi or BM25Plus) from the library
        `rank-bm25`, initialized with a valid corpus.
    @param corpus: list, array-like
        A valid list containing the corpus from which the BM25 object has been 
        initialized. As returned from function read_corpus().
    @param n_results: int, default = 1
        The number of top results to print.
    """
    
    # We skip checking validity of arguments for now... We assume the user 
    # knows what they're doing.
    
    # Get top results for the query
    top_results = bm25.get_top_n(tokenized_query, corpus, n = n_results)
    
    # Take words from each result
    top_results_id = [' '.join(top_result).split("-->")[-1] 
                             for top_result in top_results]
    
    # Return results
    return top_results_id

In [ ]:
# check queries
queries_test[0]

{'query': 'cho qua bao năm mộng buon quen dấu', 'query_id': '000'}

In [ ]:
corpus[766][1]

'Xin dâng Đảng lời thề sắc son. \nXin dâng Đảng nhung~ trái tim hồng. \nĐốt cháy cuộc đời. \nNguyện làm ngọn đuốc cháy sáng cho mọi người. \nĐể huy hoàng chói lọi một niềm tin. \nXua tan bóng đêm. \nTự hào thay những người chiến sỹ. \nQuyết hy sinh bảo vệ Đảng quang vinh.\nNhư con ong chuyên cần xây tổ. \nGiữ hương thơm mật ngọt cho đời. \nTrọn chữ tâm, tôi xin làm người lính. \nVì Đảng nguyện hiến dâng. \nVì Đảng nguyện quên mình. \nQuyết giữ trọn lời thề với non sông. \nQuyết giữ trọn những trái tim hồng. \nSáng mãi cuộc đời. \nNguyện làm ngọn đuốc cháy sáng giữa lòng người. \nĐể huy hoàng chói lọi một niềm tin. \nXua tan bóng đêm. \nTự hào thay những người chiến sỹ. \nQuyết hy sinh bảo vệ Đảng quang vinh.\nNhư con ong chuyên cần xây tổ. \nGiữ hương thơm mật ngọt cho đời. \nTrọn chữ tâm, tôi xin làm người lính. \nVì Đảng nguyện hiến dâng. \nVì Đảng nguyện quên mình.\n \n'

# Process & Export file submission

# New Section

In [ ]:
import csv
from pyvi import ViUtils
import re

with open("submission.csv", "w") as csv_writer:
  fieldnames = ['query_id', 'song_id']
  writer = csv.DictWriter(csv_writer, fieldnames=fieldnames)
  writer.writeheader()
  for ques in tqdm(queries_test):
    preprocess_query = " ".join(ques["query"].lower().replace("/", "").strip("").split())
    tokenized_query = word_tokenize(preprocess_query)
    results = bm25okapi_search(tokenized_query = tokenized_query, bm25 = bm25, corpus = tokenized_corpus, n_results = 10)
    writer.writerow({'query_id': ques["query_id"], "song_id": " ".join(results)})

ModuleNotFoundError: ignored

In [ ]:
results


['2132',
 '2480',
 '0880',
 '1675',
 '1902',
 '2236',
 '1877',
 '0683',
 '0623',
 '2377']